In [509]:
import numpy as np
from numpy.random import rand

from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
from matplotlib import cm

%matplotlib qt 

from scipy.interpolate import interp1d

In [857]:
def init_figure():
    from matplotlib.animation import FFMpegWriter
    metadata = dict(title='Double Slit Animation', artist='Drew Palmer',comment='EPS 109 Final Project')
    writer = FFMpegWriter(fps=15, metadata=metadata, bitrate=200000)
    #fig = plt.figure(dpi=200)
    fig = plt.figure(figsize=(18.,9.))
    plt.show()
    #ax1 = fig.add_subplot(121)
    #ax2 = fig.add_subplot(122)
    return fig, writer

def update_figure(fig, intensity, resolution, source_upper, source_lower, r_upper, r_lower, wall_sum, param_string):
        plt.clf()
        
        r_med =  (r_upper + r_lower) / 2
        intensity_med = resolution**2 * intensity/r_med**2
        intensity_square1 = intensity_med.reshape((resolution, resolution))
        intensity_square = intensity.reshape((resolution, resolution))
        
        ax1 = fig.add_subplot(121)
        ax1.set_aspect('equal', adjustable='box')
        ax1.set_title('Double Slit Viewed From Above')
        ax1.yaxis.tick_right()
 
        ax1.imshow(intensity_square, cmap=cm.coolwarm)  # not normalized for the 2D animation so we can see all the waves before they decay
        ax1.scatter(0, source_upper, c='lime')
        ax1.scatter(0, source_lower, c='lime')

        ax2 = fig.add_subplot(122)
        ax2.set_aspect(1000., adjustable='box')
        ax2.set_title('Amplitude at Incident Wall')
        #ax2.set_ylim(0,1.)
        
        #Instantaneous Incident Wall 1D wave
        #f = interp1d(np.linspace(0,resolution-1, resolution), intensity_square1[:,-1])
        #xnew = np.linspace(0, resolution-1, resolution*10)
        #ax2.scatter(np.linspace(0,resolution-1, resolution), intensity_square1[:,-1], c=intensity_square1[:,-1], marker='.', cmap=cm.coolwarm, linewidths=1)
        #ax2.plot(xnew, f(xnew), ':k', lw=1, alpha=.4)


        #Summed Incident Wall 1D wave
        wall_sum_normalized = wall_sum / max(wall_sum)
        ax2.scatter(np.linspace(0,resolution-1, resolution), wall_sum_normalized, c=wall_sum_normalized, marker='.', cmap=cm.coolwarm, linewidths=1)
        
        title_string = 'Double Slit Experiment: [{}]'.format(param_string)
        fig.suptitle(title_string, fontsize = 28)

        #plt.show()
        plt.draw()
        plt.pause(.01)

In [858]:
def create_meshgrid(resolution, env_length, slit_spacing):
    '''Creates two grid of points that represent distances from each source, to the respective pixel in the environemnt
    Creates locations of the upper and lower sources based on slit_spacing parameter. '''
    m = resolution / env_length
    
    source_upper = int(m*(env_length/2 + slit_spacing/2))
    source_lower = int(m*(env_length/2 - slit_spacing/2))
    
    xx = np.linspace(0,resolution-1, resolution)
    yy = np.linspace(0,resolution-1, resolution)
    X, Y = np.meshgrid(xx, yy)
    mesh_in_tuples = np.concatenate([X.reshape(-1, 1), Y.reshape(-1, 1)], axis=-1)
    
    y = mesh_in_tuples[:,1]
    y_upper = mesh_in_tuples[:,1] - source_upper
    y_lower = mesh_in_tuples[:,1] - source_lower
    x = mesh_in_tuples[:,0]
    
    r_upper = (x**2 + y_upper**2)**.5
    r_lower = (x**2 + y_lower**2)**.5
    
    return x, y, r_upper, r_lower, source_upper, source_lower

In [859]:
def time_step(resolution, it, k, frequency, total_time, iterations, r_upper, r_lower, wall_sum, amplitude_upper=1., amplitude_lower=1., c=3e8):
    '''One iteration of the time dependent light wave equation
    Evaluated the light wave equation for each source at different time steps defined by "it", then superpose the waveforms
    together and normalize. returns the normalized intensity for every point in the environment.'''
    dt = total_time/iterations
    omega = frequency * 2 * np.pi
    #k = omega / c 
    t = dt*it
    
    wave_upper = amplitude_upper*np.cos(k*r_upper - omega*t/c)
    wave_lower = amplitude_lower*np.cos(k*r_lower - omega*t/c) 
    
    #superpose the two waves
    A = (wave_upper + wave_lower)
    intensity =   A**2 / (amplitude_upper + amplitude_lower)**2 
    
    #applying inverse square law for 1D incident wall plot
    r_med =  (r_upper + r_lower) / 2
    intensity_med = resolution**2 * intensity/r_med**2
    intensity_square1 = intensity_med.reshape((resolution, resolution))
    
     
    wall_sum += (np.array(intensity_square1[:,-1])/  (amplitude_upper + amplitude_lower)**2)    
    return intensity

In [860]:
def run_sim(resolution, env_length, slit_spacing, k, frequency, total_time, iterations, param_string, 
            file_name_str, amplitude_upper=1., amplitude_lower=1., c=3e8):
    '''Run "iteration" number of iteration of time_step. This function also creates an animation and saves it to the
    current directory with file name "file_name_str".mp4. This creates a figure that pops out in a new window. The figure 
    Contains one animation of waves in 2D space where their amplitude is represented by color. I also animate the 1D wave on
    the incident wall. The 1D wave on the incident wall is a sum of the intensities form all iterations of the time_step loop. 
    This is analagous to measuring the power from photons at specific spots on the incident wall.
    
    Parameters
    ----------------------------------------------------------------------------------------------------------------
    resolution: number of pixels in one dimension of the simulation. Total pixel count is resolution**2. Expects an 
    odd integer. (example: 1001)
    env_length: length of system in meters, used for calculating real distances. Important when one cares more 
    about accuracy of the incident wall instead of the wave animation itself. (setting this to be a realistic distance,
    like 1 meter, will mean the waveform is unresolved in the animation because of how many wavelengths fit in one meter)
    expects a float.
    slit_spacing: how far in meters the slits are apart. expects a float. should not be greater than env_length.
    k: wavenumber of the photon to be simulated. When aiming for a good animation of waves use low (unrealistic k). 
    Expects a float.
    frequency: Frequency of the photon. linear frequency of the photon in question. expects a float. Frequency and k 
    should be unrelated, excpet when going for a realistic simulation of the incident wall (see above)
    total_time: the total time elapsed during the simulation in seconds. Expects a float
    iterations: number of iterations perfomed in the simulation. Expects an integer.
    param_string: Relevant parameters to be displayed in the title of the plot. Expects a string
    file_name_string: name of the file as it will be saved in current directory. Expects a string without a file type
    extension.
    amplitude_upper, amplitude_lower, amplitude of the waves coming out of the upper and lower slits respectively. They 
    should be equal for the classic diffraction pattern. Expects floats.
    '''
    
    fig, writer = init_figure()

    x, y, r_up, r_low, source_upper, source_lower = create_meshgrid(resolution, env_length, slit_spacing)
    
    #update_figure(fig, intensity, resolution, source_upper, source_lower)
    
    wall_sum = np.zeros(resolution) # array of collected photons at wall over many iterations

    filename = file_name_str + ".mp4"
    with writer.saving(fig, filename, dpi=200):
        for it in range(iterations):
            if (it%10==0): print(it,end='')
            else: print('.',end='')
            intensity = time_step(resolution, it, k, frequency, total_time, iterations, r_up, r_low, wall_sum, amplitude_upper, amplitude_lower, c)
            update_figure(fig, intensity, resolution, source_upper, source_lower, r_up, r_low, wall_sum, param_string)
            writer.grab_frame()
        print('Simulation Finished')

Run cell below to run simulation. Running this cell will save the file to current directory.

In [ ]:
# enter parameters here ###########################################################################################
resolution = int(1001)
env_length = 1     #dont change this right now
slit_spacing = .1
k=.1   # k for red laser is ~14,000 cm^-1, choosing a smaller k so I can see the waves in the animation
frequency = 4.3e14  # red laser
total_time = 100
iterations = 200
amplitude_lower=1.
amplitude_upper=1.
##################################################################################################################
# Change the file name and title name as you please or use what I have written ###################################
param_string = 'Res:{0}, d:{1}, k:{2}, Time:{3}, A:(Upper:{4}, Lower:{5})'.format(resolution, slit_spacing*(resolution-1), k, total_time, amplitude_upper, amplitude_lower)
file_name_str = 'ds_animate{0}_{1}_{2}_{3}_{4}_{5}_{6}'.format(resolution, slit_spacing*(resolution-1), k, frequency, total_time, amplitude_upper, amplitude_lower)
##################################################################################################################
run_sim(resolution, env_length, slit_spacing, k, frequency, total_time, iterations, param_string, file_name_str, 
        amplitude_upper, amplitude_lower, c=3e8)